In [1]:
# Import appropriate modules
import pandas as pd
from pathlib import Path
import tensorflow as tf
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler,OneHotEncoder
import datetime
import numpy as np
import yfinance as yf
from datetime import datetime
import hvplot
import hvplot.pandas
import matplotlib.pyplot as plt


In [2]:
def retrieve_yahoo_data(ticker = 'spy', start_date = '2007-07-01', end_date = '2021-10-03'):
    try:
        # get data based on ticker
        yahoo_data = yf.Ticker(ticker)
        print(f"Processing Ticker {ticker}")
        # select data using start date and end data and calculate the daily return
        price_df = yahoo_data.history(start=start_date, end=end_date).Close
        price_df.name = ticker
        # if no data retrieved raise exception
        if price_df.shape[0] == 0:
            raise Exception("No Prices.")
        return price_df
    # handle exception
    except Exception as ex:
        print(f"Sorry, Data not available for '{ticker}': Exception is {ex}")

In [3]:
# Set up the variable related to tickers and tickers data
ticker_data_dict = {}
ticker_list = ["^VIX", "spy", "DX-Y.NYB", "tlt", "ief", "gld", "slv", "CL=F", "USDJPY=X", "VXX"]

# Retrieve Tickers
def retrieve_tickers(ticker_data_dict, ticker_list):
    for ticker in ticker_list:
        ticker_data = retrieve_yahoo_data(ticker)
        ticker_data_dict[ticker] = ticker_data
        
    return ticker_data_dict
        
ticker_data_dict = retrieve_tickers(ticker_data_dict, ticker_list)
ticker_data_df = pd.DataFrame(ticker_data_dict)
# ticker_data_df = ticker_data_df.dropna()
# Display the ticker data related data frame
ticker_data_df.head()

Processing Ticker ^VIX
Processing Ticker spy
Processing Ticker DX-Y.NYB
Processing Ticker tlt
Processing Ticker ief
Processing Ticker gld
Processing Ticker slv
Processing Ticker CL=F
Processing Ticker USDJPY=X
Processing Ticker VXX


^VIX         spy   DX-Y.NYB        tlt        ief        gld  \
Date                                                                        
2007-07-02  15.40  114.157883  81.389999  56.094959  58.102348  65.019997   
2007-07-03  14.92  114.571541        NaN  55.752937  57.929966  64.739998   
2007-07-04    NaN         NaN        NaN        NaN        NaN        NaN   
2007-07-05  15.48  114.451218  81.540001  55.128147  57.606758  64.419998   
2007-07-06  14.72  115.052834  81.459999  54.904518  57.470306  64.959999   

               slv       CL=F    USDJPY=X  VXX  
Date                                            
2007-07-02  12.588  71.089996  122.230003  NaN  
2007-07-03  12.532        NaN  122.470001  NaN  
2007-07-04     NaN        NaN  122.660004  NaN  
2007-07-05  12.465  71.809998  122.949997  NaN  
2007-07-06  12.680  72.809998  123.360001  NaN

In [4]:
returns_df=ticker_data_df.pct_change()
returns_all_but_VIX=returns_df.drop(columns=['^VIX'])

In [5]:
cum_returns=(1+returns_df).cumprod()
cum_returns_all_but_vix=(1+returns_all_but_VIX).cumprod()
cum_returns_all_but_vix

spy  DX-Y.NYB       tlt       ief       gld       slv  \
Date                                                                     
2007-07-02       NaN       NaN       NaN       NaN       NaN       NaN   
2007-07-03  1.003624  1.000000  0.993903  0.997033  0.995694  0.995551   
2007-07-04  1.003624  1.000000  0.993903  0.997033  0.995694  0.995551   
2007-07-05  1.002570  1.001843  0.982765  0.991470  0.990772  0.990229   
2007-07-06  1.007840  1.000860  0.978778  0.989122  0.999077  1.007309   
...              ...       ...       ...       ...       ...       ...   
2021-09-27  3.877437  1.147315  2.606016  1.984771  2.516764  1.663489   
2021-09-28  3.799300  1.152107  2.565423  1.977204  2.492310  1.650779   
2021-09-29  3.805694  1.159110  2.569874  1.979268  2.481083  1.584843   
2021-09-30  3.759180  1.158005  2.569518  1.981675  2.525685  1.630124   
2021-10-01  3.803855  1.155425  2.591142  1.989765  2.531375  1.654751   

                CL=F  USDJPY=X       VXX  
Date                                      
2007-07-02       NaN       NaN       NaN  
2007-07-03  1.000000  1.001963       NaN  
2007-07-04  1.000000  1.003518       NaN  
2007-07-05  1.010128  1.005890       NaN  
2007-07-06  1.024195  1.009245       NaN  
...              ...       ...       ...  
2021-09-27  1.061331  0.906193  0.224331  
2021-09-28  1.059080  0.907829  0.247740  
2021-09-29  1.052609  0.912444  0.251356  
2021-09-30  1.055423  0.915782  0.251537  
2021-10-01  1.067379  0.911896  0.242408  

[3720 rows x 9 columns]

In [6]:
# Are levels correlated? -- YES
ticker_data_df.corr()

^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
^VIX      1.000000 -0.261907 -0.177535 -0.153038 -0.238696 -0.140994   
spy      -0.261907  1.000000  0.694249  0.885115  0.866796  0.482224   
DX-Y.NYB -0.177535  0.694249  1.000000  0.770689  0.754411  0.123592   
tlt      -0.153038  0.885115  0.770689  1.000000  0.982691  0.623439   
ief      -0.238696  0.866796  0.754411  0.982691  1.000000  0.680952   
gld      -0.140994  0.482224  0.123592  0.623439  0.680952  1.000000   
slv      -0.116533 -0.112768 -0.455048 -0.040164  0.045964  0.714587   
CL=F     -0.154325 -0.481942 -0.830481 -0.623989 -0.569718 -0.023258   
USDJPY=X -0.236938  0.529305  0.676866  0.398247  0.344841 -0.360724   
VXX       0.375032 -0.868761  0.274011 -0.356807 -0.469316 -0.539503   

               slv      CL=F  USDJPY=X       VXX  
^VIX     -0.116533 -0.154325 -0.236938  0.375032  
spy      -0.112768 -0.481942  0.529305 -0.868761  
DX-Y.NYB -0.455048 -0.830481  0.676866  0.274011  
tlt      -0.040164 -0.623989  0.398247 -0.356807  
ief       0.045964 -0.569718  0.344841 -0.469316  
gld       0.714587 -0.023258 -0.360724 -0.539503  
slv       1.000000  0.477390 -0.711848 -0.681930  
CL=F      0.477390  1.000000 -0.514512 -0.340802  
USDJPY=X -0.711848 -0.514512  1.000000  0.049850  
VXX      -0.681930 -0.340802  0.049850  1.000000

In [7]:
#Are returns correlated? YES, the most
returns_df.corr()

^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
^VIX      1.000000 -0.719043  0.093661  0.334191  0.344312 -0.010204   
spy      -0.719043  1.000000 -0.182516 -0.431965 -0.430174  0.031201   
DX-Y.NYB  0.093661 -0.182516  1.000000  0.011808 -0.053912 -0.406660   
tlt       0.334191 -0.431965  0.011808  1.000000  0.911064  0.153196   
ief       0.344312 -0.430174 -0.053912  0.911064  1.000000  0.192800   
gld      -0.010204  0.031201 -0.406660  0.153196  0.192800  1.000000   
slv      -0.164473  0.220519 -0.418170 -0.007243  0.026679  0.794172   
CL=F     -0.130616  0.173980 -0.101696 -0.120436 -0.105578  0.071690   
USDJPY=X -0.110360  0.212615  0.051795 -0.128968 -0.190356 -0.037653   
VXX       0.886326 -0.774009  0.072226  0.280663  0.311779 -0.066436   

               slv      CL=F  USDJPY=X       VXX  
^VIX     -0.164473 -0.130616 -0.110360  0.886326  
spy       0.220519  0.173980  0.212615 -0.774009  
DX-Y.NYB -0.418170 -0.101696  0.051795  0.072226  
tlt      -0.007243 -0.120436 -0.128968  0.280663  
ief       0.026679 -0.105578 -0.190356  0.311779  
gld       0.794172  0.071690 -0.037653 -0.066436  
slv       1.000000  0.124697  0.002264 -0.227686  
CL=F      0.124697  1.000000  0.035922 -0.163233  
USDJPY=X  0.002264  0.035922  1.000000 -0.013628  
VXX      -0.227686 -0.163233 -0.013628  1.000000

In [8]:
# Is the VIX level correlted with returns? -- Not do much. It's much more correlated with levels,
# or vIX returns correlated with returns

vix_level_and_price_returns_df=pd.concat([ticker_data_df['^VIX'],returns_all_but_VIX], axis=1)
vix_level_and_price_returns_df.corr()

^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
^VIX      1.000000 -0.136983  0.037840  0.071525  0.080746  0.017460   
spy      -0.136983  1.000000 -0.182516 -0.431965 -0.430174  0.031201   
DX-Y.NYB  0.037840 -0.182516  1.000000  0.011808 -0.053912 -0.406660   
tlt       0.071525 -0.431965  0.011808  1.000000  0.911064  0.153196   
ief       0.080746 -0.430174 -0.053912  0.911064  1.000000  0.192800   
gld       0.017460  0.031201 -0.406660  0.153196  0.192800  1.000000   
slv      -0.024428  0.220519 -0.418170 -0.007243  0.026679  0.794172   
CL=F     -0.075762  0.173980 -0.101696 -0.120436 -0.105578  0.071690   
USDJPY=X -0.054239  0.212615  0.051795 -0.128968 -0.190356 -0.037653   
VXX       0.223272 -0.774009  0.072226  0.280663  0.311779 -0.066436   

               slv      CL=F  USDJPY=X       VXX  
^VIX     -0.024428 -0.075762 -0.054239  0.223272  
spy       0.220519  0.173980  0.212615 -0.774009  
DX-Y.NYB -0.418170 -0.101696  0.051795  0.072226  
tlt      -0.007243 -0.120436 -0.128968  0.280663  
ief       0.026679 -0.105578 -0.190356  0.311779  
gld       0.794172  0.071690 -0.037653 -0.066436  
slv       1.000000  0.124697  0.002264 -0.227686  
CL=F      0.124697  1.000000  0.035922 -0.163233  
USDJPY=X  0.002264  0.035922  1.000000 -0.013628  
VXX      -0.227686 -0.163233 -0.013628  1.000000

In [9]:
vix_level_and_cum_price_returns_df=pd.concat([ticker_data_df['^VIX'],cum_returns_all_but_vix], axis=1)
vix_level_and_cum_price_returns_df.hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [10]:
vix_level_adjusted=ticker_data_df['^VIX']/10
vix_level_adjusted.hvplot()

:Curve   [Date]   (^VIX)

In [11]:
vix_level_adj_and_cum_price_returns_df=pd.concat([vix_level_adjusted,cum_returns_all_but_vix], axis=1)
vix_level_adj_and_cum_price_returns_df.hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [12]:
ticker_data_df[["^VIX", "VXX"]].dropna().hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [13]:
VIX_and_VXX_for_plot=pd.concat([ticker_data_df["^VIX"], ticker_data_df["VXX"]/5],axis=1).dropna()
VIX_and_VXX_for_plot.hvplot()

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [14]:
VIX_and_VXX_for_plot=pd.concat([ticker_data_df["^VIX"], ticker_data_df["VXX"]],axis=1).dropna()
returns_vix_and_vxx=VIX_and_VXX_for_plot.pct_change().dropna()
returns_vix_and_vxx.head()

^VIX       VXX
Date                          
2018-01-29  0.195164  0.069414
2018-01-30  0.068642  0.032792
2018-01-31 -0.084517  0.003273
2018-02-01 -0.005170 -0.050343
2018-02-02  0.285078  0.128594

In [15]:
# Cases of interest
# When both go up together
vix_and_vxx_positive_df=returns_vix_and_vxx[(returns_vix_and_vxx["^VIX"]*returns_vix_and_vxx['VXX']>0) & 
                     (returns_vix_and_vxx["^VIX"]>0)]

In [16]:
# It is 3% a good threshold? It would if most of the time vxx is also positive when vix is above threshold
results=[]

for threshold_bps in range(150,1000,5):
    threshold=threshold_bps/10000
    returns_vxx_negative_with_vix_above_threshold=returns_vix_and_vxx[(returns_vix_and_vxx["^VIX"]>threshold) &
                                                                  (returns_vix_and_vxx["VXX"]<0)]

                                                                  
    cases_vxx_negative_and_vix_above_threshold=returns_vxx_negative_with_vix_above_threshold.describe().iloc[0,0]
    cases_vix_above_threshold=returns_vix_and_vxx[returns_vix_and_vxx["^VIX"]>threshold].describe().iloc[0,0]
    
    results.append({'Threshold return (%)':threshold*100, 
                     "cases_vxx_negative_and_vix_above_threshold":cases_vxx_negative_and_vix_above_threshold,
                     "cases_vix_above_threshold":cases_vix_above_threshold,
                     "Proportion of fail cases (%)": cases_vxx_negative_and_vix_above_threshold/cases_vix_above_threshold*100
                    })
    
results_df=pd.DataFrame(results)

results_df.head(50)

Threshold return (%)  cases_vxx_negative_and_vix_above_threshold  \
0                   1.50                                        38.0   
1                   1.55                                        38.0   
2                   1.60                                        37.0   
3                   1.65                                        36.0   
4                   1.70                                        36.0   
5                   1.75                                        36.0   
6                   1.80                                        32.0   
7                   1.85                                        30.0   
8                   1.90                                        29.0   
9                   1.95                                        27.0   
10                  2.00                                        27.0   
11                  2.05                                        27.0   
12                  2.10                                        27.0   
13                  2.15                                        27.0   
14                  2.20                                        27.0   
15                  2.25                                        24.0   
16                  2.30                                        24.0   
17                  2.35                                        20.0   
18                  2.40                                        19.0   
19                  2.45                                        19.0   
20                  2.50                                        18.0   
21                  2.55                                        18.0   
22                  2.60                                        16.0   
23                  2.65                                        16.0   
24                  2.70                                        16.0   
25                  2.75                                        15.0   
26                  2.80                                        14.0   
27                  2.85                                        11.0   
28                  2.90                                        11.0   
29                  2.95                                        11.0   
30                  3.00                                        11.0   
31                  3.05                                        11.0   
32                  3.10                                        10.0   
33                  3.15                                        10.0   
34                  3.20                                        10.0   
35                  3.25                                        10.0   
36                  3.30                                        10.0   
37                  3.35                                         8.0   
38                  3.40                                         7.0   
39                  3.45                                         6.0   
40                  3.50                                         6.0   
41                  3.55                                         5.0   
42                  3.60                                         4.0   
43                  3.65                                         4.0   
44                  3.70                                         4.0   
45                  3.75                                         4.0   
46                  3.80                                         4.0   
47                  3.85                                         4.0   
48                  3.90                                         4.0   
49                  3.95                                         4.0   

    cases_vix_above_threshold  Proportion of fail cases (%)  
0                       334.0                     11.377246  
1                       333.0                     11.411411  
2                       330.0                     11.212121  
3                       325.0                     11.076923  
4                    

In [17]:
curve=results_df.hvplot(x='Threshold return (%)', 
                  y='Proportion of fail cases (%)',
                  title='Determination of Threshold for VIX return prediction'
                 )
amount_of_cases=results_df[(results_df['Threshold return (%)']>2) &
                           (results_df['Threshold return (%)']<4)].hvplot.bar(x='Threshold return (%)', 
                  y=['cases_vxx_negative_and_vix_above_threshold','cases_vix_above_threshold'],
                  title='Determination of Threshold for VIX return prediction'
                 )
curve+amount_of_cases

:Layout
   .Curve.I :Curve   [Threshold return (%)]   (Proportion of fail cases (%))
   .Bars.I  :Bars   [Threshold return (%),Variable]   (value)

In [18]:
# Read the google_trends_df.csv file from the Resources folder into a Pandas DataFrame
df_path = Path("./Resources/google_trends_df.csv")
google_trends_df = pd.read_csv(df_path,index_col= 'Date', parse_dates= True, infer_datetime_format=True)

# Review the DataFrame
google_trends_df


Leading_Indicators  PMI  CCI  Jobless_Claims  GDP  war  \
Date                                                                 
2004-01-01                   0    0    0               0   31   50   
2004-02-01                   0    0    0               0   61   41   
2004-03-01                   0    0    0               0   20   63   
2004-04-01                   0    0    0               0   60   40   
2004-05-01                   0    0    0               0   28   73   
...                        ...  ...  ...             ...  ...  ...   
2021-06-01                   7    0    0               0   15   37   
2021-07-01                   0    0    0               5   14   52   
2021-08-01                   3    0    0              10   15   38   
2021-09-01                   0    0    0               5   23   41   
2021-10-01                   0    0    0               0   21   11   

            Impeachment  Catastrophe  Natural_disaster  Inflation  ...  \
Date                                                               ...   
2004-01-01            0           34                 0         84  ...   
2004-02-01            0           51                 0         55  ...   
2004-03-01            0           43                 0         41  ...   
2004-04-01            0           50                 0         77  ...   
2004-05-01            0           30                27         58  ...   
...                 ...          ...               ...        ...  ...   
2021-06-01            1           16                 7         80  ...   
2021-07-01            1           18                 6         60  ...   
2021-08-01           13           15                 5         53  ...   
2021-09-01           86           31                 7         48  ...   
2021-10-01            0            0                 0         32  ...   

            Debt_ceiling  retail_spending  Consumer_spending  Consumer  \
Date                                                                     
2004-01-01             0                0                  0       100   
2004-02-01             0                0                  0        78   
2004-03-01             0                0                  0        95   
2004-04-01             0                0                  0        74   
2004-05-01             0                0                  0        88   
...                  ...              ...                ...       ...   
2021-06-01             0                0                  5        43   
2021-07-01             1                0                  5        46   
2021-08-01             1                0                  0        45   
2021-09-01            12                0                  5        45   
2021-10-01            38                0                  0        59   

            Earnings  Economic_contraction  Depression  Shock  \
Date                                                            
2004-01-01        45                     0          37     34   
2004-02-01        51                     0           0      0   
2004-03-01        36                     0           0     85   
2004-04-01        74                     0          36     33   
2004-05-01        37                     0          49     30   
...              ...                   ...         ...    ...   
2021-06-01        33                     0          17     21   
2021-07-01        47                     0          27     31   
2021-08-01        48                     0          17     24   
2021-09-01        65                     0          28     20   
2021-10-01        66                     0          25      0   

            Monetary_policy  VIX  
Date                              
2004-01-01                0    0  
2004-02-01               74    0  
2004-03-01                0   17  
2004-04-01                0    6  
2004-05-01              100    6  
...                     ...  ...  
2021-06-01                5   18  
2021-07-01    

In [19]:
# Review the data types associated with the columns
google_trends_df.dtypes

Leading_Indicators      int64
PMI                     int64
CCI                     int64
Jobless_Claims          int64
GDP                     int64
war                     int64
Impeachment             int64
Catastrophe             int64
Natural_disaster        int64
Inflation               int64
unemployment            int64
Market_crash            int64
Covid                   int64
virus                   int64
Pandemic                int64
vaccination             int64
Delta                   int64
Covid_mutation          int64
FED                     int64
Tapering                int64
Liquidity               int64
Banking                 int64
Correction_of_market    int64
coup                    int64
Debt_ceiling            int64
retail_spending         int64
Consumer_spending       int64
Consumer                int64
Earnings                int64
Economic_contraction    int64
Depression              int64
Shock                   int64
Monetary_policy         int64
VIX       

In [38]:
ticker_data_df1= ticker_data_df.drop(columns="VXX")
gtd_tdf = pd.concat([google_trends_df, ticker_data_df1.pct_change()],axis=1).dropna()
gtd_tdf.head()

Leading_Indicators  PMI  CCI  Jobless_Claims   GDP   war  \
Date                                                                   
2007-08-01                 0.0  0.0  0.0             0.0  23.0  25.0   
2007-10-01                18.0  0.0  0.0             0.0  14.0  50.0   
2007-11-01                 0.0  0.0  0.0             0.0  35.0  54.0   
2008-01-01                17.0  0.0  0.0             0.0  22.0  68.0   
2008-02-01                 0.0  0.0  0.0             0.0  66.0  51.0   

            Impeachment  Catastrophe  Natural_disaster  Inflation  ...   VIX  \
Date                                                               ...         
2007-08-01          0.0         30.0               0.0       45.0  ...  21.0   
2007-10-01          0.0         12.0               0.0       65.0  ...  10.0   
2007-11-01          0.0         19.0               7.0       79.0  ...  16.0   
2008-01-01          0.0         21.0               0.0       52.0  ...  18.0   
2008-02-01          0.0         25.0               0.0       74.0  ...   6.0   

                ^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
Date                                                                     
2007-08-01  0.006378  0.004873  0.001238 -0.002165 -0.002771  0.002128   
2007-10-01 -0.008889  0.011272  0.002316  0.005714  0.001197  0.005305   
2007-11-01  0.252563 -0.023408  0.001438  0.012993  0.008162 -0.008776   
2008-01-01  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2008-02-01 -0.083206  0.016088  0.003591  0.006011  0.003245 -0.022429   

                 slv      CL=F  USDJPY=X  
Date                                      
2007-08-01  0.006874 -0.021481  0.004729  
2007-10-01 -0.000659 -0.017389  0.009238  
2007-11-01 -0.024861 -0.011002 -0.008060  
2008-01-01  0.000000  0.000000  0.001523  
2008-02-01 -0.011833 -0.030409  0.002438  

[5 rows x 43 columns]

In [39]:
# Set the Signal column
gtd_tdf["Signal"] = 0.0

# Generate the trading signals 1 (entry) or -1 (exit)
# where 1 is when the ^VIX is greater than 3.6%.
# where 0 is when the ^VIX  is less than 3.6%.
for index, row in gtd_tdf.iterrows():
    if row["^VIX"] > 0.036:
        gtd_tdf.loc[index, "Signal"] = 1.0
    if row["^VIX"] < 0.036:
        gtd_tdf.loc[index,"Signal"] =  0.0
# Review the DataFrame
gtd_tdf.head()        


Leading_Indicators  PMI  CCI  Jobless_Claims   GDP   war  \
Date                                                                   
2007-08-01                 0.0  0.0  0.0             0.0  23.0  25.0   
2007-10-01                18.0  0.0  0.0             0.0  14.0  50.0   
2007-11-01                 0.0  0.0  0.0             0.0  35.0  54.0   
2008-01-01                17.0  0.0  0.0             0.0  22.0  68.0   
2008-02-01                 0.0  0.0  0.0             0.0  66.0  51.0   

            Impeachment  Catastrophe  Natural_disaster  Inflation  ...  \
Date                                                               ...   
2007-08-01          0.0         30.0               0.0       45.0  ...   
2007-10-01          0.0         12.0               0.0       65.0  ...   
2007-11-01          0.0         19.0               7.0       79.0  ...   
2008-01-01          0.0         21.0               0.0       52.0  ...   
2008-02-01          0.0         25.0               0.0       74.0  ...   

                ^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
Date                                                                     
2007-08-01  0.006378  0.004873  0.001238 -0.002165 -0.002771  0.002128   
2007-10-01 -0.008889  0.011272  0.002316  0.005714  0.001197  0.005305   
2007-11-01  0.252563 -0.023408  0.001438  0.012993  0.008162 -0.008776   
2008-01-01  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2008-02-01 -0.083206  0.016088  0.003591  0.006011  0.003245 -0.022429   

                 slv      CL=F  USDJPY=X  Signal  
Date                                              
2007-08-01  0.006874 -0.021481  0.004729     0.0  
2007-10-01 -0.000659 -0.017389  0.009238     0.0  
2007-11-01 -0.024861 -0.011002 -0.008060     1.0  
2008-01-01  0.000000  0.000000  0.001523     0.0  
2008-02-01 -0.011833 -0.030409  0.002438     0.0  

[5 rows x 44 columns]

In [40]:
# Define the target set y using the Signal column
y = gtd_tdf["Signal"].values
# Display a sample of y
y

array([0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1., 0.,
       1., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 1.,
       0., 0., 0., 1., 0., 0., 0., 0., 1., 0., 1., 0., 0., 0., 0., 1., 1.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,
       1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 1., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1.,
       0., 1., 1., 0., 0., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1.,
       0., 0., 0.])

In [41]:
# Define features set X by selecting all columns but Signal
X = gtd_tdf.drop(columns=["Signal"])

# Review the features DataFrame
X.head()

Leading_Indicators  PMI  CCI  Jobless_Claims   GDP   war  \
Date                                                                   
2007-08-01                 0.0  0.0  0.0             0.0  23.0  25.0   
2007-10-01                18.0  0.0  0.0             0.0  14.0  50.0   
2007-11-01                 0.0  0.0  0.0             0.0  35.0  54.0   
2008-01-01                17.0  0.0  0.0             0.0  22.0  68.0   
2008-02-01                 0.0  0.0  0.0             0.0  66.0  51.0   

            Impeachment  Catastrophe  Natural_disaster  Inflation  ...   VIX  \
Date                                                               ...         
2007-08-01          0.0         30.0               0.0       45.0  ...  21.0   
2007-10-01          0.0         12.0               0.0       65.0  ...  10.0   
2007-11-01          0.0         19.0               7.0       79.0  ...  16.0   
2008-01-01          0.0         21.0               0.0       52.0  ...  18.0   
2008-02-01          0.0         25.0               0.0       74.0  ...   6.0   

                ^VIX       spy  DX-Y.NYB       tlt       ief       gld  \
Date                                                                     
2007-08-01  0.006378  0.004873  0.001238 -0.002165 -0.002771  0.002128   
2007-10-01 -0.008889  0.011272  0.002316  0.005714  0.001197  0.005305   
2007-11-01  0.252563 -0.023408  0.001438  0.012993  0.008162 -0.008776   
2008-01-01  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2008-02-01 -0.083206  0.016088  0.003591  0.006011  0.003245 -0.022429   

                 slv      CL=F  USDJPY=X  
Date                                      
2007-08-01  0.006874 -0.021481  0.004729  
2007-10-01 -0.000659 -0.017389  0.009238  
2007-11-01 -0.024861 -0.011002 -0.008060  
2008-01-01  0.000000  0.000000  0.001523  
2008-02-01 -0.011833 -0.030409  0.002438  

[5 rows x 43 columns]

In [42]:
# Split the preprocessed data into a training and testing dataset
# Assign the function a random_state equal to 1
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)


In [43]:
# Create a StandardScaler instance
scaler = StandardScaler()

# Fit the scaler to the features training dataset
X_scaler = scaler.fit(X_train)

# Fit the scaler to the features training dataset
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)


In [44]:
# Define the the number of inputs (features) to the model
number_input_features = X.shape[1]

# Review the number of features
number_input_features

43

In [45]:
# Define the number of neurons in the output layer
number_output_neurons = 1

In [46]:
# Define the number of hidden nodes for the first hidden layer - use the square root of the number of input features times number of output neurons
hidden_nodes_layer1 =  int(np.ceil(np.sqrt(number_input_features * number_output_neurons)))

# Review the number hidden nodes in the first layer
hidden_nodes_layer1

7

In [47]:
# Define the number of hidden nodes for the second hidden layer - hidden layer neurons divided by 2
hidden_nodes_layer2 =  int(np.floor(hidden_nodes_layer1/2))

# Review the number hidden nodes in the second layer
hidden_nodes_layer2

3

In [48]:
# Create the Sequential model instance
nn = Sequential()

In [49]:
# Add the first hidden layer
nn.add(Dense(input_dim=number_input_features, units=hidden_nodes_layer1, activation="relu"))

In [50]:
# Add the second hidden layer
nn.add(Dense(units=hidden_nodes_layer2, activation="relu"))

In [51]:
# Add the output layer to the model specifying the number of output neurons and activation function
nn.add(Dense(units=number_output_neurons, activation="sigmoid"))

In [52]:
# Display the Sequential model summary
nn.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_3 (Dense)              (None, 7)                 308       
_________________________________________________________________
dense_4 (Dense)              (None, 3)                 24        
_________________________________________________________________
dense_5 (Dense)              (None, 1)                 4         
Total params: 336
Trainable params: 336
Non-trainable params: 0
_________________________________________________________________


In [53]:
# Compile the Sequential model
nn.compile(loss="binary_crossentropy", optimizer="adam", metrics=["accuracy"])

In [54]:
# Fit the model using 50 epochs and the training data
model_1 = nn.fit(X_train_scaled, y_train, epochs=50)

Epoch 1/50
3/3 [==============================] - 0s 2ms/step - loss: 1.2863 - accuracy: 0.2198
Epoch 2/50
3/3 [==============================] - 0s 2ms/step - loss: 1.2445 - accuracy: 0.2198
Epoch 3/50
3/3 [==============================] - 0s 3ms/step - loss: 1.2083 - accuracy: 0.2308
Epoch 4/50
3/3 [==============================] - 0s 3ms/step - loss: 1.1701 - accuracy: 0.2418
Epoch 5/50
3/3 [==============================] - 0s 2ms/step - loss: 1.1362 - accuracy: 0.2418
Epoch 6/50
3/3 [==============================] - 0s 3ms/step - loss: 1.1011 - accuracy: 0.2637
Epoch 7/50
3/3 [==============================] - 0s 3ms/step - loss: 1.0711 - accuracy: 0.2637
Epoch 8/50
3/3 [==============================] - 0s 2ms/step - loss: 1.0389 - accuracy: 0.2637
Epoch 9/50
3/3 [==============================] - 0s 3ms/step - loss: 1.0114 - accuracy: 0.2967
Epoch 10/50
3/3 [==============================] - 0s 2ms/step - loss: 0.9800 - accuracy: 0.3077
Epoch 11/50
3/3 [======================

In [55]:
# Evaluate the model loss and accuracy metrics using the evaluate method and the test data
model_loss, model_accuracy = nn.evaluate(X_test_scaled, y_test, verbose=2)

# Display the model loss and accuracy results
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

1/1 - 0s - loss: 0.4443 - accuracy: 0.8710
Loss: 0.44430044293403625, Accuracy: 0.8709677457809448
